In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn
from bokeh.io import output_notebook, show, export_png
from bokeh.plotting import figure
from bokeh.io import show, output_file
from bokeh.plotting import figure
from selenium import webdriver
from phantomjs_bin import executable_path
from bokeh.models import Plot, Title, Circle, ColumnDataSource, LinearAxis, Range1d, PrintfTickFormatter, AdaptiveTicker, SingleIntervalTicker
from pandas.plotting import table

output_notebook()
%matplotlib inline
data = pd.read_csv('matavimo_data galutinis.csv')


Loading BokehJS ...

In [2]:
data.head()

Time     Ax, g     Ay, g     Az, g   Wx, dps   Wy, dps   Wz, dps  \
0  19:56:53 -0.000162  0.000443  0.000653  0.008987 -0.012120 -0.006311   
1  19:56:54  0.000103  0.000393  0.000516  0.000731 -0.005625 -0.005168   
2  19:56:55 -0.000060  0.000018 -0.000868  0.004105 -0.003205  0.002173   
3  19:56:56 -0.000053 -0.000258 -0.000174 -0.007435  0.006397  0.004055   
4  19:56:57 -0.000971 -0.000089 -0.001225 -0.001948  0.000919  0.001181   

        T, C    Ax2, g    Ay2, g  ...  Wy2, dps  Wz2, dps      T2, C  \
0  18.025055 -0.000020  0.000282  ...  0.000201  0.001106  17.933645   
1  18.034428 -0.000009  0.000202  ... -0.000449  0.000219  17.936308   
2  18.032045  0.000057  0.000031  ...  0.001025  0.000997  17.928629   
3  18.049259 -0.000078  0.000062  ... -0.000727  0.000701  17.928892   
4  18.044756  0.000052  0.000245  ... -0.000125 -0.000477  17.927702   

     Ax3, g    Ay3, g    Az3, g  Wx3, dps  Wy3, dps  Wz3, dps      T3, C  
0 -0.000009 -0.000025  0.000075 -0.000039 -0.000060 -0.000421  17.075027  
1 -0.000103 -0.000095 -0.000071 -0.000440  0.000809 -0.000744  17.055880  
2 -0.000010 -0.000025  0.000043  0.000051 -0.000118 -0.000975  17.048067  
3 -0.000037 -0.000068  0.000015  0.000181  0.000068 -0.000262  17.056541  
4 -0.000064 -0.000090 -0.000016 -0.000051 -0.000146 -0.000457  17.060911  

[5 rows x 22 columns]

# Vidurkių skaičiavimas

In [3]:
# Vertimas i m/s^2 

data.loc[:,'Ax, g'] *= 78.17898234
data.loc[:,'Ay, g'] *= 78.17898234
data.loc[:,'Az, g'] *= 78.17898234
 
data.loc[:,'Ax2, g'] *= 79.16723387
data.loc[:,'Ay2, g'] *= 79.16723387
data.loc[:,'Az2, g'] *= 79.16723387

data.loc[:,'Ax3, g'] *= 80.11298989
data.loc[:,'Ay3, g'] *= 80.11298989
data.loc[:,'Az3, g'] *= 80.11298989


In [4]:
# Vidrukinimas

data['AxV, g'] = data.loc[:, ["Ax, g","Ax2, g","Ax3, g"]].astype(float).mean(axis=1)
data['AyV, g'] = data.loc[:, ["Ay, g","Ay2, g","Ay3, g"]].astype(float).mean(axis=1)
data['AzV, g'] = data.loc[:, ["Az, g","Az2, g","Az3, g"]].astype(float).mean(axis=1)

data['WxV, dps'] = data.loc[:, ["Wx, dps","Wx2, dps","Wx3, dps"]].astype(float).mean(axis=1)
data['WyV, dps'] = data.loc[:, ["Wy, dps","Wy2, dps","Wy3, dps"]].astype(float).mean(axis=1)
data['WzV, dps'] = data.loc[:, ["Wz, dps","Wz2, dps","Wz3, dps"]].astype(float).mean(axis=1)

data['TV, C'] = data.loc[:, ["T, C","T2, C","T3, C"]].astype(float).mean(axis=1)

In [5]:
# Integravimas i greiti

data['Vx, m/s']  = data.loc[:, ["Ax, g"]].cumsum()
data['Vy, m/s']  = data.loc[:, ["Ay, g"]].cumsum()
data['Vz, m/s']  = data.loc[:, ["Az, g"]].cumsum()

data['Vx2, m/s']  = data.loc[:, ["Ax2, g"]].cumsum()
data['Vy2, m/s']  = data.loc[:, ["Ay2, g"]].cumsum()
data['Vz2, m/s']  = data.loc[:, ["Az2, g"]].cumsum()

data['Vx3, m/s']  = data.loc[:, ["Ax3, g"]].cumsum()
data['Vy3, m/s']  = data.loc[:, ["Ay3, g"]].cumsum()
data['Vz3, m/s']  = data.loc[:, ["Az3, g"]].cumsum()

data['VxV, m/s']  = data.loc[:, ["AxV, g"]].cumsum()
data['VyV, m/s']  = data.loc[:, ["AyV, g"]].cumsum()
data['VzV, m/s']  = data.loc[:, ["AzV, g"]].cumsum()

In [6]:
# Integravimas i atstuma

data['Sx, m']  = data.loc[:, ["Vx, m/s"]].cumsum()
data['Sy, m']  = data.loc[:, ["Vy, m/s"]].cumsum()
data['Sz, m']  = data.loc[:, ["Vz, m/s"]].cumsum()

data['Sx2, m']  = data.loc[:, ["Vx2, m/s"]].cumsum()
data['Sy2, m']  = data.loc[:, ["Vy2, m/s"]].cumsum()
data['Sz2, m']  = data.loc[:, ["Vz2, m/s"]].cumsum()

data['Sx3, m']  = data.loc[:, ["Vx3, m/s"]].cumsum()
data['Sy3, m']  = data.loc[:, ["Vy3, m/s"]].cumsum()
data['Sz3, m']  = data.loc[:, ["Vz3, m/s"]].cumsum()

data['SxV, m']  = data.loc[:, ["VxV, m/s"]].cumsum()
data['SyV, m']  = data.loc[:, ["VyV, m/s"]].cumsum()
data['SzV, m']  = data.loc[:, ["VzV, m/s"]].cumsum()

In [7]:
# Integravimas i kampa

data['Gx, deg']  = data.loc[:, ["Wx, dps"]].cumsum()
data['Gy, deg']  = data.loc[:, ["Wy, dps"]].cumsum()
data['Gz, deg']  = data.loc[:, ["Wz, dps"]].cumsum()

data['Gx2, deg']  = data.loc[:, ["Wx2, dps"]].cumsum()
data['Gy2, deg']  = data.loc[:, ["Wy2, dps"]].cumsum()
data['Gz2, deg']  = data.loc[:, ["Wz2, dps"]].cumsum()

data['Gx3, deg']  = data.loc[:, ["Wx3, dps"]].cumsum()
data['Gy3, deg']  = data.loc[:, ["Wy3, dps"]].cumsum()
data['Gz3, deg']  = data.loc[:, ["Wz3, dps"]].cumsum()

data['GxV, deg']  = data.loc[:, ["WxV, dps"]].cumsum()
data['GyV, deg']  = data.loc[:, ["WyV, dps"]].cumsum()
data['GzV, deg']  = data.loc[:, ["WzV, dps"]].cumsum()

# Statistika

## Standartinis nuokrypis skirtinguose jutikliuose

In [8]:
# Kuriama lentelė
std = pd.DataFrame()
std['']  = ['Ax, g', 'Ay, g', 'Az, g', 'Wx, dps', 'Wy, dps', 'Wz, dps', 'T, C']
std['Pirmas jutiklis']  = data.loc[:, ['Ax, g', 'Ay, g', 'Az, g', 'Wx, dps', 'Wy, dps', 'Wz, dps', 'T, C']].std(axis=0).reset_index(drop=True)
std['Antras jutiklis']  = data.loc[:, ['Ax2, g', 'Ay2, g', 'Az2, g', 'Wx2, dps', 'Wy2, dps', 'Wz2, dps', 'T2, C']].std(axis=0).reset_index(drop=True)
std['Trecias jutiklis']  = data.loc[:, ['Ax3, g', 'Ay3, g', 'Az3, g', 'Wx3, dps', 'Wy3, dps', 'Wz3, dps', 'T3, C']].std(axis=0).reset_index(drop=True)
std['Vidurkis']  = data.loc[:, ['AxV, g', 'AyV, g', 'AzV, g', 'WxV, dps', 'WyV, dps', 'WzV, dps', 'TV, C']].std(axis=0).reset_index(drop=True)

# Renkamas mažiausias standartinis nuokrypis
std.loc[std.min(axis=1) == std.loc[:,'Pirmas jutiklis'], 'Maziausias standartinis nuokrypis'] = 'Pirmo'
std.loc[std.min(axis=1) == std.loc[:,'Antras jutiklis'], 'Maziausias standartinis nuokrypis'] = 'Antro'
std.loc[std.min(axis=1) == std.loc[:,'Vidurkis'], 'Maziausias standartinis nuokrypis'] = 'Vidurkio'
std.loc[std.min(axis=1) == std.loc[:,'Trecias jutiklis'], 'Maziausias standartinis nuokrypis'] = 'Trečio'


In [9]:
std

Pirmas jutiklis  Antras jutiklis  Trecias jutiklis  Vidurkis  \
0    Ax, g         0.031161         0.004139          0.003956  0.010573   
1    Ay, g         0.018419         0.008319          0.003344  0.006802   
2    Az, g         0.042809         0.005245          0.005177  0.014444   
3  Wx, dps         0.006106         0.001684          0.000519  0.002166   
4  Wy, dps         0.007523         0.001051          0.000853  0.002534   
5  Wz, dps         0.004064         0.001504          0.000588  0.001453   
6     T, C         0.151418         0.156708          0.166448  0.157763   

  Maziausias standartinis nuokrypis  
0                            Trečio  
1                            Trečio  
2                            Trečio  
3                            Trečio  
4                            Trečio  
5                            Trečio  
6                             Pirmo

# Grafikai

## Akselerometras

In [10]:
p = figure(plot_width=800, plot_height=400, title="Akselerometro pagreičio kitimas Ax, m/s^2")
p.line(data.index, data['Ax, g'],legend="Ax, m/s^2", line_width=2)
p.line(data.index, data['Ax2, g'],legend="Ax2, m/s^2", color='green', line_width=2)
p.line(data.index, data['Ax3, g'],legend="Ax3, m/s^2", color='orange', line_width=2)
p.line(data.index, data['AxV, g'],legend="AxV, m/s^2",color='red', line_width=2)
p.xaxis.axis_label = 't, s'
p.yaxis.axis_label = 'm/s'

show(p) 

In [11]:
p = figure(plot_width=800, plot_height=400, title="Akselerometro pagreičio kitimas Ay, m/s^2")
p.line(data.index, data['Ay, g'],legend="Ay, m/s^2", line_width=2)
p.line(data.index, data['Ay2, g'],legend="Ay2, m/s^2",color='green', line_width=2)
p.line(data.index, data['Ay3, g'],legend="Ay3, m/s^2",color='orange', line_width=2)
p.line(data.index, data['AyV, g'],legend="AyV, m/s^2",color='red', line_width=2)
p.xaxis.axis_label = 't, s'
p.yaxis.axis_label = 'Ay, m/s^2'
show(p) 

In [12]:
p = figure(plot_width=800, plot_height=400, title="Akselerometro pagreičio kitimas Az, m/s^2")
p.line(data.index, data['Az, g'],legend="Az, m/s^2", line_width=2)
p.line(data.index, data['Az2, g'],legend="Az2, m/s^2",color='green', line_width=2)
p.line(data.index, data['Az3, g'],legend="Az3, m/s^2",color='orange', line_width=2)
p.line(data.index, data['AzV, g'],legend="AzV, m/s^2",color='red', line_width=2)
p.xaxis.axis_label = 't, s'
p.yaxis.axis_label = 'Az, m/s^2'
p.legend
show(p) 

## Giroskopas

In [13]:
p = figure(plot_width=800, plot_height=400, title="Giroskopo kampinis greitis Wx, dps")
p.line(data.index, data['Wx, dps'],legend="Wx, dps", line_width=2)
p.line(data.index, data['Wx2, dps'],legend="Wx2, dps",color='green', line_width=2)
p.line(data.index, data['Wx3, dps'],legend="Wx3, dps",color='orange', line_width=2)
p.line(data.index, data['WxV, dps'],legend="WxV, dps",color='red', line_width=2)
p.xaxis.axis_label = 't, s'
p.yaxis.axis_label = 'Wx, dps'
p.legend
show(p) 

In [14]:
p = figure(plot_width=800, plot_height=400, title="Giroskopo kampinis greitis Wy, °/s")
p.line(data.index, data['Wy, dps'],legend="Wy, dps", line_width=2)
p.line(data.index, data['Wy2, dps'],legend="Wy2, dps",color='green', line_width=2)
p.line(data.index, data['Wy3, dps'],legend="Wy3, dps",color='green', line_width=2)
p.line(data.index, data['WyV, dps'],legend="WyV, dps",color='red', line_width=2)
p.xaxis.axis_label = 't, s'
p.yaxis.axis_label = 'Wy, dps'
p.legend
show(p) 

In [15]:
p = figure(plot_width=800, plot_height=400, title="Giroskopo kampinis greitis Wz, °/s")
p.line(data.index, data['Wz, dps'],legend="Wz, dps", line_width=2)
p.line(data.index, data['Wz2, dps'],legend="Wz2, dps",color='green', line_width=2)
p.line(data.index, data['Wz3, dps'],legend="Wz3, dps",color='orange', line_width=2)
p.line(data.index, data['WzV, dps'],legend="WzV, dps",color='red', line_width=2)
p.xaxis.axis_label = 't, s'
p.yaxis.axis_label = 'Wz, dps'
p.legend
show(p) 

## Temperatūra

In [16]:
p = figure(plot_width=800, plot_height=400, title="T, °C")
p.line(data.index, data['T, C'],legend="T, °C", line_width=2)
p.line(data.index, data['T2, C'],legend="T2, °C",color='green', line_width=2)
p.line(data.index, data['T3, C'],legend="T3, °C",color='orange', line_width=2)
p.line(data.index, data['TV, C'],legend="TV, °C",color='red', line_width=2)
p.xaxis.axis_label = 't, s'
p.yaxis.axis_label = 'T, °C'
p.legend
show(p) 

# Integravimai

## Greitis

In [17]:
p = figure(plot_width=800, plot_height=400, title="Akselerometro greitis Vx, m/s")
p.line(data.index, data['Vx, m/s'],legend="Vx, m/s", line_width=2)
p.line(data.index, data['Vx2, m/s'],legend="Vx2, m/s", color='green', line_width=2)
p.line(data.index, data['Vx3, m/s'],legend="Vx3, m/s", color='orange', line_width=2)
p.line(data.index, data['VxV, m/s'],legend="VxV, m/s",color='red', line_width=2)
p.xaxis.axis_label = 't, s'
p.yaxis.axis_label = 'Vx, m/s'
show(p) 

In [18]:
p = figure(plot_width=800, plot_height=400, title="Akselerometro greitis Vy, m/s")
p.line(data.index, data['Vy, m/s'],legend="Vy, m/s", line_width=2)
p.line(data.index, data['Vy2, m/s'],legend="Vy2, m/s", color='green', line_width=2)
p.line(data.index, data['Vy3, m/s'],legend="Vy3, m/s", color='orange', line_width=2)
p.line(data.index, data['VyV, m/s'],legend="VyV, m/s",color='red', line_width=2)
p.xaxis.axis_label = 't, s'
p.yaxis.axis_label = 'Vy, m/s'
show(p) 

In [19]:
p = figure(plot_width=800, plot_height=400, title="Akselerometro greitis Vz, m/s")
p.line(data.index, data['Vz, m/s'], legend="Vz, m/s", line_width=2)
p.line(data.index, data['Vz2, m/s'],legend="Vz2, m/s", color='green', line_width=2)
p.line(data.index, data['Vz3, m/s'],legend="Vz3, m/s", color='orange', line_width=2)
p.line(data.index, data['VzV, m/s'],legend="VzV, m/s",color='red', line_width=2)
p.xaxis.axis_label = 't, s'
p.yaxis.axis_label = 'Vz, m/s'
show(p) 

## Atstumas 

In [20]:
p = figure(plot_width=800, plot_height=400, title="Akselerometro atstumas Sx, m")
p.line(data.index, data['Sx, m'], legend="Sx, m", line_width=2)
p.line(data.index, data['Sx2, m'],legend="Sx2, m", color='green', line_width=2)
p.line(data.index, data['Sx3, m'],legend="Sx3, m", color='orange', line_width=2)
p.line(data.index, data['SxV, m'],legend="SxV, m",color='red', line_width=2)
p.xaxis.axis_label = 't, s'
p.yaxis.axis_label = 'S, m'
p.yaxis.formatter = PrintfTickFormatter(format="%4.1e")
show(p) 

In [21]:
p = figure(plot_width=800, plot_height=400, title="Akselerometro atstumas Sy, m")
p.line(data.index, data['Sy, m'], legend="Sy, m", line_width=2)
p.line(data.index, data['Sy2, m'],legend="Sy2, m", color='green', line_width=2)
p.line(data.index, data['Sy3, m'],legend="Sy3, m", color='orange', line_width=2)
p.line(data.index, data['SyV, m'],legend="SyV, m",color='red', line_width=2)
p.xaxis.axis_label = 't, s'
p.yaxis.axis_label = 'S, m'
show(p) 

In [22]:
p = figure(plot_width=800, plot_height=400, title="Akselerometro atstumas Sz, m")
p.line(data.index, data['Sz, m'], legend="Sz, m", line_width=2)
p.line(data.index, data['Sz2, m'],legend="Sz2, m", color='green', line_width=2)
p.line(data.index, data['Sz3, m'],legend="Sz3, m", color='orange', line_width=2)
p.line(data.index, data['SzV, m'],legend="SzV, m",color='red', line_width=2)
p.xaxis.axis_label = 't, s'
p.yaxis.axis_label = 'S, m'
p.yaxis.formatter = PrintfTickFormatter(format="%4.1e")
show(p) 

## Integravimo metu gautas poslinkio kampas

In [23]:
p = figure(plot_width=800, plot_height=400, title="Integravimo metu gautas poslinkio kampas Gx, deg")
p.line(data.index, data['Gx, deg'], legend="Gx, deg", line_width=2)
p.line(data.index, data['Gx2, deg'],legend="Gx2, deg", color='green', line_width=2)
p.line(data.index, data['Gx3, deg'],legend="Gx3, deg", color='orange', line_width=2)
p.line(data.index, data['GxV, deg'],legend="GxV, deg",color='red', line_width=2)
p.xaxis.axis_label = 't, s'
p.yaxis.axis_label = 'α, deg'
show(p) 

In [24]:
p = figure(plot_width=800, plot_height=400, title="Integravimo metu gautas poslinkio kampas Gy, deg")
p.line(data.index, data['Gy, deg'], legend="Gy, deg", line_width=2)
p.line(data.index, data['Gy2, deg'],legend="Gy2, deg", color='green', line_width=2)
p.line(data.index, data['Gy3, deg'],legend="Gy3, deg", color='orange', line_width=2)
p.line(data.index, data['GyV, deg'],legend="GyV, deg",color='red', line_width=2)
p.xaxis.axis_label = 't, s'
p.yaxis.axis_label = 'α, deg'
show(p) 

In [25]:
p = figure(plot_width=800, plot_height=400, title="Integravimo metu gautas poslinkio kampas Gz, dps")
p.line(data.index, data['Gz, deg'], legend="Gz, dps", line_width=2)
p.line(data.index, data['Gz2, deg'],legend="Gz2, dps", color='green', line_width=2)
p.line(data.index, data['Gz3, deg'],legend="Gz3, dps", color='orange', line_width=2)
p.line(data.index, data['GzV, deg'],legend="GV, dps",color='red', line_width=2)
p.xaxis.axis_label = 't, s'
p.yaxis.axis_label = 'α, deg'
show(p) 

# Temperatūrinės priklausomybės

In [26]:
p = figure(plot_width=800, plot_height=350, title="Ax priklausomybe nuo T")
p.scatter(data['T, C'], data['Ax, g'], legend="Ax", line_width=0.1)

p.xaxis.axis_label = 'T, °C'
p.yaxis.axis_label = 'Ax, m/s^2'
show(p) 


In [27]:
p = figure(plot_width=800, plot_height=400, title="Ay priklausomybe nuo T")
p.scatter(data['T, C'], data['Ay, g'], legend="Ay", line_width=0.1)

p.xaxis.axis_label = 'T, °C'
p.yaxis.axis_label = 'Ay, m/s2'
show(p) 

In [28]:
p = figure(plot_width=800, plot_height=400, title="Az priklausomybe nuo T")
p.scatter(data['T, C'], data['Az, g'], legend="Az", line_width=0.1)
p.xaxis.axis_label = 'T, °C'
p.yaxis.axis_label = 'Az, m/s2'
show(p) 

In [29]:
p = figure(plot_width=900, plot_height=400, title="Wx priklausomybe nuo T")
p.scatter(data['T, C'], data['Wx, dps'], legend="Wx, dps", line_width=0.1)
p.scatter(data['T, C'], data['Wx2, dps'],legend="Wx2, dps", color='green', line_width=0.1)
p.scatter(data['T, C'], data['Wx3, dps'],legend="Wx3, dps", color='orange', line_width=0.1)


p.xaxis.axis_label = 'T, °C'
p.yaxis.axis_label = 'Wx, dps'
show(p) 

In [30]:
p = figure(plot_width=900, plot_height=400, title="Wy priklausomybe nuo T")
p.scatter(data['T, C'], data['Wy, dps'], legend="Wy, dps", line_width=0.1)
p.scatter(data['T, C'], data['Wy2, dps'],legend="Wy2, dps", color='green', line_width=0.1)
p.scatter(data['T, C'], data['Wy3, dps'],legend="Wy3, dps", color='orange', line_width=0.1)

p.xaxis.axis_label = 'T, °C'
p.yaxis.axis_label = 'Wy, dps'
show(p) 

In [31]:
p = figure(plot_width=900, plot_height=400, title="Wz priklausomybe nuo T")
p.scatter(data['T, C'], data['Wz, dps'], legend="Wz, dps", line_width=0.1)
p.scatter(data['T, C'], data['Wz2, dps'],legend="Wz2, dps", color='green', line_width=0.1)
p.scatter(data['T, C'], data['Wz3, dps'],legend="Wz3, dps", color='orange', line_width=0.1)

p.xaxis.axis_label = 'T, °C'
p.yaxis.axis_label = 'Wz, dps'
show(p) 

# Ax histogramos

In [32]:
re, edges = np.histogram(data['Ax, g'], bins=20, weights = np.ones_like(data.index) / len(data.index))
p1 = figure(plot_width=300, plot_height=300) 
p1.quad(top=re, bottom=0, left=edges[:-1], right=edges[1:], line_color="white")
p1.xaxis.axis_label = 'Ax, m/s^2'
p1.yaxis.axis_label = 'P'
show(p1)

In [33]:
re, edges = np.histogram(data['Ax2, g'], bins=20, weights = np.ones_like(data.index) / len(data.index))
p1 = figure(plot_width=300, plot_height=300) 
p1.quad(top=re, bottom=0, left=edges[:-1], right=edges[1:], color='green', line_color="white")
p1.xaxis.axis_label = 'Ax2, m/s^2'
p1.yaxis.axis_label = 'P'
show(p1)

In [34]:
re, edges = np.histogram(data['Ax3, g'], bins=20, weights = np.ones_like(data.index) / len(data.index))
p1 = figure(plot_width=300, plot_height=300) 
p1.quad(top=re, bottom=0, left=edges[:-1], right=edges[1:], color='orange', line_color="white")
p1.xaxis.axis_label ='Ax3, m/s^2'
p1.yaxis.axis_label = 'P'
show(p1)

In [35]:
re, edges = np.histogram(data['AxV, g'], bins=20, weights = np.ones_like(data.index) / len(data.index))
p1 = figure(plot_width=300, plot_height=300) 
p1.quad(top=re, bottom=0, left=edges[:-1], right=edges[1:], color='red', line_color="white")
p1.xaxis.axis_label ='AxV, m/s^2'
p1.yaxis.axis_label = 'P'
show(p1)

# Ay histogramos

In [36]:
re, edges = np.histogram(data['Ay, g'], bins=20, weights = np.ones_like(data.index) / len(data.index))
p2 = figure(plot_width=300, plot_height=300) 
p2.quad(top=re, bottom=0, left=edges[:-1], right=edges[1:], line_color="white")
p2.xaxis.axis_label ='Ay, m/s^2'
p2.yaxis.axis_label = 'P'
show(p2)

In [37]:
re, edges = np.histogram(data['Ay2, g'], bins=20, weights = np.ones_like(data.index) / len(data.index))
p2 = figure(plot_width=300, plot_height=300) 
p2.quad(top=re, bottom=0, left=edges[:-1], right=edges[1:], color= 'green', line_color="white")
p2.xaxis.axis_label ='Ay2, m/s^2'
p2.yaxis.axis_label = 'P'
show(p2)

In [38]:
re, edges = np.histogram(data['Ay3, g'], bins=20, weights = np.ones_like(data.index) / len(data.index))
p2 = figure(plot_width=300, plot_height=300) 
p2.quad(top=re, bottom=0, left=edges[:-1], right=edges[1:], color='orange', line_color="white")
p2.xaxis.axis_label ='Ay3, m/s^2'
p2.yaxis.axis_label = 'P'
show(p2)

In [39]:
re, edges = np.histogram(data['AyV, g'], bins=20, weights = np.ones_like(data.index) / len(data.index))
p2 = figure(plot_width=300, plot_height=300) 
p2.quad(top=re, bottom=0, left=edges[:-1], right=edges[1:], color='red', line_color="white")
p2.xaxis.axis_label ='AyV, m/s^2'
p2.yaxis.axis_label = 'P'
show(p2)

# Az histogramos

In [40]:
re, edges = np.histogram(data['Az, g'], bins=20, weights = np.ones_like(data.index) / len(data.index))
p3 = figure(plot_width=300, plot_height=300) 
p3.quad(top=re, bottom=0, left=edges[:-1], right=edges[1:], line_color="white")
p3.xaxis.axis_label ='Az, m/s^2'
p3.yaxis.axis_label = 'P'
show(p3)

In [41]:
re, edges = np.histogram(data['Az2, g'], bins=20, weights = np.ones_like(data.index) / len(data.index))
p3 = figure(plot_width=300, plot_height=300) 
p3.quad(top=re, bottom=0, left=edges[:-1], right=edges[1:], color='green', line_color="white")
p3.xaxis.axis_label ='Az2, m/s^2'
p3.yaxis.axis_label = 'P'
show(p3)

In [42]:
re, edges = np.histogram(data['Az3, g'], bins=20, weights = np.ones_like(data.index) / len(data.index))
p3 = figure(plot_width = 300, plot_height=300) 
p3.quad(top=re, bottom=0, left=edges[:-1], right=edges[1:], color='orange', line_color="white")
p3.xaxis.axis_label ='Az3, m/s^2'
p3.yaxis.axis_label = 'P'
show(p3)

In [43]:
re, edges = np.histogram(data['AzV, g'], bins=20, weights = np.ones_like(data.index) / len(data.index))
p3 = figure(plot_width=300, plot_height=300) 
p3.quad(top=re, bottom=0, left=edges[:-1], right=edges[1:], color='red', line_color="white")
p3.xaxis.axis_label ='AzV, m/s^2'
p3.yaxis.axis_label = 'P'
show(p3)

# Wx histogramos

In [44]:
re, edges = np.histogram(data['Wx, dps'], bins=20, weights = np.ones_like(data.index) / len(data.index))
p4 = figure(plot_width=300, plot_height=300) 
p4.quad(top=re, bottom=0, left=edges[:-1], right=edges[1:], line_color="white")
p4.xaxis.axis_label ='Wx, dps'
p4.yaxis.axis_label = 'P'
show(p4)

In [45]:
re, edges = np.histogram(data['Wx2, dps'], bins=20, weights = np.ones_like(data.index) / len(data.index))
p4 = figure(plot_width=300, plot_height=300) 
p4.quad(top=re, bottom=0, left=edges[:-1], right=edges[1:], color='green', line_color="white")
p4.xaxis.axis_label ='Wx2, dps'
p4.yaxis.axis_label = 'P'
show(p4)

In [46]:
re, edges = np.histogram(data['Wx3, dps'], bins=20, weights = np.ones_like(data.index) / len(data.index))
p4 = figure(plot_width=300, plot_height=300) 
p4.quad(top=re, bottom=0, left=edges[:-1], right=edges[1:], color='orange', line_color="white")
p4.xaxis.axis_label ='Wx3, dps'
p4.yaxis.axis_label = 'P'
show(p4)

In [47]:
re, edges = np.histogram(data['WxV, dps'], bins=20, weights = np.ones_like(data.index) / len(data.index))
p4 = figure(plot_width=300, plot_height=300) 
p4.quad(top=re, bottom=0, left=edges[:-1], right=edges[1:], color='red', line_color="white")
p4.xaxis.axis_label ='WxV, dps'
p4.yaxis.axis_label = 'P'
p4.xgrid[0].ticker.desired_num_ticks = 5
show(p4)

# Wy histogramos

In [48]:
re, edges = np.histogram(data['Wy, dps'], bins=20, weights = np.ones_like(data.index) / len(data.index))
p5 = figure(plot_width=300, plot_height=300) 
p5.quad(top=re, bottom=0, left=edges[:-1], right=edges[1:], line_color="white")
p5.xaxis.axis_label ='Wy, dps'
p5.yaxis.axis_label = 'P'
show(p5)

In [49]:
re, edges = np.histogram(data['Wy2, dps'], bins=20, weights = np.ones_like(data.index) / len(data.index))
p5 = figure(plot_width=300, plot_height=300) 
p5.quad(top=re, bottom=0, left=edges[:-1], right=edges[1:], color='green', line_color="white")
p5.xaxis.axis_label ='Wy2, dps'
p5.yaxis.axis_label = 'P'
p5.xgrid[0].ticker.desired_num_ticks = 5
show(p5)

In [50]:
re, edges = np.histogram(data['Wy3, dps'], bins=20, weights = np.ones_like(data.index) / len(data.index))
p5 = figure(plot_width=300, plot_height=300) 
p5.quad(top=re, bottom=0, left=edges[:-1], right=edges[1:], color='orange', line_color="white")
p5.xaxis.axis_label ='Wy3, dps'
p5.yaxis.axis_label = 'P'
p5.xaxis.formatter = PrintfTickFormatter(format="%4.1e")
show(p5)

In [51]:
re, edges = np.histogram(data['WyV, dps'], bins=20, weights = np.ones_like(data.index) / len(data.index))
p5 = figure(plot_width=300, plot_height=300) 
p5.quad(top=re, bottom=0, left=edges[:-1], right=edges[1:], color='red', line_color="white")
p5.xaxis.axis_label ='WyV, dps'
p5.yaxis.axis_label = 'P'
show(p5)

# Wz histogramos

In [52]:
re, edges = np.histogram(data['Wz, dps'], bins=20, weights = np.ones_like(data.index) / len(data.index))
p6 = figure(plot_width=300, plot_height=300) 
p6.quad(top=re, bottom=0, left=edges[:-1], right=edges[1:], line_color="white")
p6.xaxis.axis_label ='Wz, dps'
p6.yaxis.axis_label = 'P'
show(p6)

In [53]:
re, edges = np.histogram(data['Wz2, dps'], bins=20, weights = np.ones_like(data.index) / len(data.index))
p6 = figure(plot_width=300, plot_height=300) 
p6.quad(top=re, bottom=0, left=edges[:-1], right=edges[1:], color='green', line_color="white")
p6.xaxis.axis_label ='Wz2, dps'
p6.yaxis.axis_label = 'P'
p6.xaxis.formatter = PrintfTickFormatter(format="%4.1e")
p6.xgrid[0].ticker.desired_num_ticks = 4
show(p6)

In [54]:
re, edges = np.histogram(data['Wz3, dps'], bins=20, weights = np.ones_like(data.index) / len(data.index))
p6 = figure(plot_width=300, plot_height=300) 
p6.quad(top=re, bottom=0, left=edges[:-1], right=edges[1:], color='orange', line_color="white")
p6.xaxis.axis_label ='Wz3, dps'
p6.yaxis.axis_label = 'P'
show(p6)

In [55]:
re, edges = np.histogram(data['WzV, dps'], bins=20, weights = np.ones_like(data.index) / len(data.index))
p6 = figure(plot_width=300, plot_height=300) 
p6.quad(top=re, bottom=0, left=edges[:-1], right=edges[1:], color='red', line_color="white")
p6.xaxis.axis_label ='WzV, dps'
p6.yaxis.axis_label = 'P'
show(p6)